# Ein- und Ausgabe I/O

zahlreiche Varianten und Funktionen, das Folgende ist eine kleine Auswahl

## Konsole

- OS-abhängig; üblicherweise 3 Kanäle _(streams)_: `stdin, stdout, stderr`  (Standardinput, -output, -errorkanal)



- Schreiben nach `stdout`: `print()`,`println()`,`printstyled()`
- Schreiben nach `stderr`:  `print(strerr,...)`, `println(stderr,...)`, `printstyled(stderr,...)`
- Lesen von `stdin`: `readline()`

### Umwandeln von Strings in andere Typen:
  
  - `chomp()` entfernt newline
  - `split()` zerlegt in "Wörter" 
  - `parse()` wandelt in andere Typen um

### Buffer

- `write`-Zugriffe werden gebuffert.
  
  - `flush(stdout)`   leert Buffer

In [1]:
# aus dem ersten Beispielprogramm

function input(prompt = "Eingabe:")
    println(prompt)
    flush(stdout)
    return chomp(readline())
end


input (generic function with 2 methods)

In [2]:
a = input("Bitte 2 Zahlen eingeben!")

Bitte 2 Zahlen eingeben!
stdin> 33 67


"33 67"

In [3]:
av = split(a)

2-element Vector{SubString{String}}:
 "33"
 "67"

In [4]:
parse.(Int, av)

2-element Vector{Int64}:
 33
 67

In [5]:
# Ausgaben auf den Fehlerkanal stderr erscheinen im Jupyter in rot:

println(stderr, "Das sollte nicht passieren!")    

Das sollte nicht passieren!


### Einzelne Tastenanschläge einlesen

- `readline()` u.ä. warten auf den Abschluss der Eingabe durch Drücken der `Enter`-Taste. 
- Zum Einlesen einzelner _keystrokes_:
  
  - [https://stackoverflow.com/questions/56888266/how-to-read-keyboard-inputs-at-every-keystroke-in-julia](https://stackoverflow.com/questions/56888266/how-to-read-keyboard-inputs-at-every-keystroke-in-julia)
  - [https://stackoverflow.com/questions/60954235/how-can-i-test-whether-stdin-has-input-available-in-julia](https://stackoverflow.com/questions/60954235/how-can-i-test-whether-stdin-has-input-available-in-julia)
  

## Formatierte Ausgabe mit dem `Printf`-Paket

Die Macros `@sprintf` und `@printf` sind den gleichnamigen C-Funktionen nachempfunden

- Formatstring: Normaler String mit Platzhaltern
- Platzhalter haben die Form 
```
%[flags][width][.precision]type
```
   (wobei die Angaben in eckigen Klammern alle optional sind)
- Typen: 
```
%s      string
%i      integer
%o      integer octal (base=8)
%x, %X  integer hexadecimal (base=16) with digits 0-9abcdef  or 0-9ABCDEF, resp.
%f      floatong point number
%e      floating point number, scientific representation
%g      floating point, uses %f or %e depending on value
```

- Flags:
```
Pluszeichen:    rechtsbündig (Standard)
Minuszeichen:   linksbündig
Null:           mit führenden Nullen
```

- Width: 
```
Anzahl der minimal verwendeten Zeichen (wenn nötig, werden auch mehr genommen)
```


Zeit für Beispiele:

In [6]:
using Printf    # Paket laden nicht vergessen!

In [7]:
@printf("|%s|", "Hallo")     # string mit Platzhalter für String

|Hallo|

In [8]:
@printf("|%10s|", "Hallo")   # Minimallänge, rechtsbündig    

|     Hallo|

In [9]:
@printf("|%-10s|", "Hallo")     # linksbündig

|Hallo     |

In [10]:
@printf("|%3s|", "Hallo")     # Längenangabe kann überschritten werden 
                              # besser eine 'kaputt formatierte' Tabelle als falsche Werte!!

|Hallo|

In [11]:
j = 123
k = 90019001
l = 3342678

@printf("j= %012i, k= %-12i, l = %12i", j, k, l)   #  0-Flag für führende Nullen

j= 000000000123, k= 90019001    , l =      3342678

`@printf` und `@sprintf` können wie alle Macros wie Funktionen aufgerufen werden:

In [12]:
@printf("%i %i", 22, j)

22 123

-- oder wie Macros, also ohne Funktionsklammern und ohne Komma:

In [13]:
@printf "%i %i" 22 j

22 123

`@printf` kann als erstes Argument noch einen stream übergeben bekommen. 

Ansonsten besteht die Argumentliste aus

- Formatstring mit Platzhaltern
- Variablen in der Reihenfolge der Platzhalter, in Anzahl und Typ zu den Platzhaltern passend

In [14]:
@printf(stderr, "Erstes Resultat: %i %s\nZweites Resultat %i", 
                                   j, "(geschätzt)"       ,k)

Erstes Resultat: 123 (geschätzt)
Zweites Resultat 90019001

`@sprintf` druckt nichts, sondern liefert den ausgefüllten formatierten String zurück: 

In [15]:
str = @sprintf("x = %10.6f", π );

In [16]:
str

"x =   3.141593"

##### Formatierung der Gleitkommazahlen:

Bedeutung des _Precision_-Wertes:

- `%f` und  `%e`-Format:  max. Anzahl der Nachkommastellen
- `%g`-Format:  max. Anzahl von ausgegebenen Ziffern (Vor- + Nachkommastellen) 

In [17]:
x = 123456.7890123456

@printf("%20.4f   %20.4e", x, x)     # 4 Nachkommastellen

         123456.7890             1.2346e+05

In [18]:
@printf("%20.7f %20.7e", x, x)     # 7 Nachkommastellen

      123456.7890123        1.2345679e+05

In [19]:
@printf("%20.7g %20.4g", x, x)    # insgesamt 7 bzw. 4 Stellen

            123456.8            1.235e+05

## Dateioperationen

Dateien werden

 - geöffnet ==>  Dabei ensteht ein neues _stream_-Objekt (zusätzlich zu `stdin, stdout, stderr`)
 - dann kann dieser _stream_ gelesen und geschrieben werden
 - geschlossen ==> _stream_-Objekt wird von Datei getrennt
 
 ```
 stream = open(path, mode)
 ```
 
 - path: Dateiname/pfad
 - mode: 
 ```
 "r"    read, öffnet am Dateianfang
 "w"    write, öffnet am Dateianfang (Datei wird neu angelegt oder überschrieben)
 "a"    append, öffnet zum Weiterschreiben am Dateiende
 ```  

In [20]:
f = open("datei.txt", "w")

IOStream(<file datei.txt>)

In [21]:
@printf(f, "%20i\n", k)

In [22]:
println(f, " zweite Zeile")

In [23]:
close(f)

In [24]:
;cat datei.txt

            90019001
 zweite Zeile


In [25]:
f = open("datei.txt", "r")

IOStream(<file datei.txt>)

In [26]:
n = 0
for i in readlines(f)    # Lese zeilenweise
    n += 1
    println(n, i)       # Drucke mit Zeilennummer
end

1            90019001
2 zweite Zeile


## Pakete für Dateiformate

Pakete für die Ein- und Ausgabe in den verschiedensten Dateiformaten 

- [PrettyTables.jl](https://ronisbr.github.io/PrettyTables.jl/stable/) Ausgabe von formatierten Tabellen
- [DelimitedFiles.jl](https://docs.julialang.org/en/v1/stdlib/DelimitedFiles/) Ein- und Ausgabe von Matrizen u.ä.
- [CSV.jl](https://csv.juliadata.org/stable/) Ein- und Ausgabe von Dateien mit "comma-delimited values" u.ä.
- [XLSX.jl](https://felipenoris.github.io/XLSX.jl/stable/tutorial/) Ein- und Ausgabe von Excel-Dateien

und viele andere mehr...

### Delimited Files


In [27]:
using DelimitedFiles

In [28]:
A = rand(200,3)

200×3 Matrix{Float64}:
 0.340458   0.825769   0.10208
 0.0268893  0.949268   0.908559
 0.649896   0.395813   0.353179
 0.14032    0.291844   0.830224
 0.63363    0.276789   0.831877
 0.524021   0.246762   0.419489
 0.585347   0.880953   0.608495
 0.777373   0.387001   0.0595369
 0.347182   0.991371   0.72133
 0.418528   0.478036   0.955822
 0.602542   0.84481    0.755724
 0.19726    0.48635    0.223986
 0.488213   0.32438    0.640762
 ⋮                     
 0.0109543  0.464666   0.0338036
 0.424558   0.739999   0.69583
 0.958684   0.432141   0.809327
 0.562518   0.273888   0.232715
 0.779498   0.0941955  0.447725
 0.65658    0.236674   0.0702908
 0.240148   0.216886   0.31698
 0.878407   0.453928   0.715879
 0.387353   0.864377   0.0140109
 0.818247   0.30614    0.724261
 0.699524   0.204064   0.308865
 0.07843    0.104628   0.715755

In [29]:
f = open("data2.txt", "w")

IOStream(<file data2.txt>)

In [30]:
writedlm(f, A)

In [31]:
close(f)

In [32]:
;head data2.txt

0.3404584106811863	0.8257693260643905	0.10208011760128599
0.026889328033128268	0.9492675653854479	0.9085591450702581
0.6498963717719178	0.3958125045190971	0.35317912384984795
0.14032004382389018	0.2918439613799869	0.8302239965868584
0.633630005283942	0.2767888491501992	0.8318766514610799
0.5240208117170729	0.24676197726593674	0.41948911446627135
0.585346515700062	0.8809527810080108	0.6084948567669999
0.7773727819682476	0.38700114682941644	0.05953685007070941
0.34718210294604357	0.9913709382217284	0.7213300130637681
0.41852821927063044	0.47803588615962034	0.9558221787263325


In [33]:
B = readdlm("data2.txt")


200×3 Matrix{Float64}:
 0.340458   0.825769   0.10208
 0.0268893  0.949268   0.908559
 0.649896   0.395813   0.353179
 0.14032    0.291844   0.830224
 0.63363    0.276789   0.831877
 0.524021   0.246762   0.419489
 0.585347   0.880953   0.608495
 0.777373   0.387001   0.0595369
 0.347182   0.991371   0.72133
 0.418528   0.478036   0.955822
 0.602542   0.84481    0.755724
 0.19726    0.48635    0.223986
 0.488213   0.32438    0.640762
 ⋮                     
 0.0109543  0.464666   0.0338036
 0.424558   0.739999   0.69583
 0.958684   0.432141   0.809327
 0.562518   0.273888   0.232715
 0.779498   0.0941955  0.447725
 0.65658    0.236674   0.0702908
 0.240148   0.216886   0.31698
 0.878407   0.453928   0.715879
 0.387353   0.864377   0.0140109
 0.818247   0.30614    0.724261
 0.699524   0.204064   0.308865
 0.07843    0.104628   0.715755

In [34]:
# man kann open() auch als 1.Argument eine function(iostream) übergeben, die auf den stream 
# angewendet wird, wonach der stream automatisch geschlosssen wird.  
#
# Mit der do-Notation sieht obiger code so aus:

open("data2.txt", "w") do io
    writedlm(io, A)
end


### CSV und DataFrames

- [DataFrames.jl](https://dataframes.juliadata.org/stable/) ist ein Paket zum bequemen Umgang mit tabellarischen Daten



In [35]:
using CSV, DataFrames, Downloads

In [36]:
# Wetterdaten von Westerland, s. https://dev.meteostat.net/bulk/hourly.html


url = "https://bulk.meteostat.net/v2/hourly/10018.csv.gz"

"https://bulk.meteostat.net/v2/hourly/10018.csv.gz"

In [37]:
http_response = Downloads.download(url)

"/tmp/jl_R2uC9y"

In [38]:
file = CSV.File(http_response, header=false)

161343-element CSV.File:
 CSV.Row: (Column1 = Dates.Date("1989-03-18"), Column2 = 7, Column3 = 6.0, Column4 = missing, Column5 = missing, Column6 = missing, Column7 = missing, Column8 = 270, Column9 = 11.2, Column10 = missing, Column11 = missing, Column12 = missing, Column13 = missing)
 CSV.Row: (Column1 = Dates.Date("1989-03-18"), Column2 = 8, Column3 = 6.0, Column4 = -1.9, Column5 = 57, Column6 = missing, Column7 = missing, Column8 = 250, Column9 = 11.2, Column10 = missing, Column11 = missing, Column12 = missing, Column13 = missing)
 CSV.Row: (Column1 = Dates.Date("1989-03-18"), Column2 = 9, Column3 = 7.0, Column4 = -3.0, Column5 = 49, Column6 = missing, Column7 = missing, Column8 = 250, Column9 = 14.8, Column10 = missing, Column11 = missing, Column12 = missing, Column13 = missing)
 CSV.Row: (Column1 = Dates.Date("1989-03-18"), Column2 = 10, Column3 = 7.0, Column4 = -1.9, Column5 = 53, Column6 = missing, Column7 = missing, Column8 = 250, Column9 = 18.4, Column10 = missing, Column11 =

In [39]:
# https://dev.meteostat.net/bulk/hourly.html#endpoints

# Spalte 1  Datum
#        2  Uhrzeit (Stunde)
#        3  Temp
#        5  Luftfeuchtigkeit
#        6  Niederschlag
#        8 Windrichtung
#        9 Windstärke


df =  DataFrame(file)

161343×13 DataFrame
    Row │ Column1     Column2  Column3   Column4    Column5  Column6   Column7 ⋯
        │ Date        Int64    Float64?  Float64?   Int64?   Float64?  Missing ⋯
────────┼───────────────────────────────────────────────────────────────────────
      1 │ 1989-03-18        7       6.0  missing    missing   missing  missing ⋯
      2 │ 1989-03-18        8       6.0       -1.9       57   missing  missing
      3 │ 1989-03-18        9       7.0       -3.0       49   missing  missing
      4 │ 1989-03-18       10       7.0       -1.9       53   missing  missing
      5 │ 1989-03-18       11       8.0       -1.0       53   missing  missing ⋯
      6 │ 1989-03-18       12       8.0        0.0       57   missing  missing
      7 │ 1989-03-18       13       8.0       -1.0       53   missing  missing
      8 │ 1989-03-18       14       8.0        0.0       57   missing  missing
      9 │ 1989-03-18       15       8.0        0.0       57   missing  missing ⋯
     10 │ 1989-03-23        9       7.0       -0.9       57   missing  missing
     11 │ 1989-03-23       10       7.0       -0.9       57   missing  missing
   ⋮    │     ⋮          ⋮        ⋮          ⋮         ⋮        ⋮         ⋮    ⋱
 161334 │ 2022-06-20       12      14.3       10.1       76   missing  missing
 161335 │ 2022-06-20       18      18.0       13.9       77   missing  missing ⋯
 161336 │ 2022-06-21        0      14.9       10.9       77   missing  missing
 161337 │ 2022-06-21        6      13.4        9.8       79   missing  missing
 161338 │ 2022-06-21       12      14.5       10.9       79   missing  missing
 161339 │ 2022-06-21       18      18.1       14.6       80   missing  missing ⋯
 161340 │ 2022-06-22        0      15.2       11.6       79   missing  missing
 161341 │ 2022-06-22        6      13.2        9.6       79   missing  missing
 161342 │ 2022-06-22       12      15.0       11.2       78   missing  missing
 161343 │ 2022-06-22       18      18.8       15.1       79   missing  missing ⋯
                                               6 columns and 161322 rows omitted

In [40]:
describe(df)

13×7 DataFrame
 Row │ variable  mean       min         median      max         nmissing  elty ⋯
     │ Symbol    Union…     Any         Any         Any         Int64     Type ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ Column1              1989-03-18  2010-09-21  2022-06-22         0  Date ⋯
   2 │ Column2   11.7822    0           12.0        23                 0  Int6
   3 │ Column3   10.5158    -14.0       11.0        34.0            1250  Unio
   4 │ Column4   6.91075    -18.1       7.0         25.0            1603  Unio
   5 │ Column5   79.9007    18          82.0        100             1603  Unio ⋯
   6 │ Column6   0.0932762  0.0         0.0         5.0           125723  Unio
   7 │ Column7                                                    161343  Miss
   8 │ Column8   208.597    0           230.0       360             2216  Unio
   9 │ Column9   22.9206    0.0         22.3        211.3            304  Unio ⋯
  10 │ Column10  37.1644    5.5         35.2        105.6         127105  Unio
  11 │ Column11  1014.08    970.0       1015.0      1049.0        116873  Unio
  12 │ Column12                                                   161343  Miss
  13 │ Column13  4.58144    0           4.0         25            124875  Unio ⋯
                                                                1 column omitted

In [41]:
using StatsPlots

In [42]:
using Dates

In [43]:
# neue Spalte mit Sp.1 und 2  (date & time) kombiniert

df[!, :datetime] = DateTime.(df.Column1) .+ Hour.(df.Column2);   

In [44]:
describe(df)

14×7 DataFrame
 Row │ variable  mean       min                  median               max      ⋯
     │ Symbol    Union…     Any                  Any                  Any      ⋯
─────┼──────────────────────────────────────────────────────────────────────────
   1 │ Column1              1989-03-18           2010-09-21           2022-06- ⋯
   2 │ Column2   11.7822    0                    12.0                 23
   3 │ Column3   10.5158    -14.0                11.0                 34.0
   4 │ Column4   6.91075    -18.1                7.0                  25.0
   5 │ Column5   79.9007    18                   82.0                 100      ⋯
   6 │ Column6   0.0932762  0.0                  0.0                  5.0
   7 │ Column7                                                       
   8 │ Column8   208.597    0                    230.0                360
   9 │ Column9   22.9206    0.0                  22.3                 211.3    ⋯
  10 │ Column10  37.1644    5.5                  35.2                 105.6
  11 │ Column11  1014.08    970.0                1015.0               1049.0
  12 │ Column12                                                      
  13 │ Column13  4.58144    0                    4.0                  25       ⋯
  14 │ datetime             1989-03-18T07:00:00  2010-09-21T21:00:00  2022-06-
                                                               3 columns omitted

In [45]:
@df df plot(:datetime, :Column3)

In [46]:
@df df plot(:datetime, [:Column9, :Column6, :Column3], 
            xlims = (DateTime(2022,1,1), DateTime(2022,7,1)), 
            layout=(3,1), title=["Wind" "Regen" "Temp"], legend=:none)